In [ ]:
# !pip install gdown
!pip install ipython-autotime
!pip install umap-learn

In [ ]:
%load_ext autotime

time: 246 µs (started: 2021-02-26 13:22:18 +00:00)


In [ ]:
# !gdown https://drive.google.com/uc?id=1yQuJlP_Igc5W2zZUEgupwvj9SNSfUTRV
!gdown https://drive.google.com/uc?id=1AEn8P631y-pq6szgAbTm538oM6waf-5E

Downloading...
From: https://drive.google.com/uc?id=1AEn8P631y-pq6szgAbTm538oM6waf-5E
To: /content/author_embedding.csv
683MB [00:07, 96.3MB/s]
time: 10.5 s (started: 2021-02-26 13:25:43 +00:00)


In [ ]:
import pandas as pd
doc_2_vec_embeddings = pd.read_csv("author_embedding.csv", header=None, index_col=0)
doc_2_vec_embeddings

1         2         3    ...       254       255       256
0                                         ...                              
1036332    -0.155256  0.260346  0.225399  ... -0.640803 -0.851161 -0.584914
1101850    -1.042691  0.059498  0.525740  ...  0.096496  0.029991 -0.762944
1336878    -0.689841  0.183287  0.197919  ... -0.607820  1.061965 -0.418734
1515524    -0.157730  0.515563  1.100034  ...  0.042994 -0.190372 -0.686180
1606427    -2.586875  0.497515 -0.283361  ...  1.306690 -0.413302 -0.836433
...              ...       ...       ...  ...       ...       ...       ...
2908387141 -0.149186  0.059576  1.266709  ... -0.109325 -0.352533 -0.162939
2908425732 -0.081930 -0.698139  0.098003  ... -1.062008  0.648366 -3.153230
2908436250  0.000000  0.000000  0.000000  ...  0.000000  0.000000  0.000000
2908499439  0.286835 -0.839971  0.611096  ...  0.714365  0.201030 -0.125780
2908506980 -0.112762 -0.300636 -0.746002  ... -1.097304 -1.068148 -2.013633

[231239 rows x 256 columns]

time: 11 s (started: 2021-02-26 13:28:21 +00:00)


In [ ]:
import numpy as np
from tqdm.notebook import tqdm
from collections import OrderedDict

# embeddings_dict = np.load("author_to_embeddings_scibert_uncased.npy", allow_pickle=True).item()
embeddings_dict = {}
for i, row in tqdm(doc_2_vec_embeddings.iterrows():
    embeddings_dict[i] = np.array(row)
embeddings_dict

{1036332: array([-1.55256040e-01,  2.60345770e-01,  2.25398650e-01, -1.46140550e-01,
        -1.21847870e-01, -6.95546050e-01, -3.25143050e-01, -4.54055000e-02,
        -3.54348470e-01,  2.59525590e-01,  3.25150330e-01,  1.82431160e-01,
         3.10491080e-01,  8.53520480e-01, -2.85897520e-01, -6.10025340e-01,
         4.03819480e-01, -1.04862190e-01, -1.63645980e-01,  2.16602780e-01,
        -1.76128870e-01,  1.32749400e-01, -1.92937680e-01, -1.84534880e-01,
        -4.13795550e-01, -3.22187930e-01,  3.68108090e-01,  1.38463770e-01,
         9.14663700e-02,  1.59419320e-01,  2.77031800e-02,  1.04432333e+00,
         7.95599150e-01,  2.78984650e-01, -1.11840290e-01,  7.46984150e-01,
        -6.91631800e-01, -2.64606300e-01, -2.64173260e-01, -6.58235110e-01,
         4.84444100e-02, -9.63084380e-01, -1.22107428e+00, -5.99012530e-01,
        -9.14333700e-02, -1.16080821e+00, -6.61597780e-01, -3.20160250e-01,
        -6.14197130e-01, -3.71133330e-01, -3.68668290e-01,  7.57273110e-01,
   

time: 16.1 s (started: 2021-02-26 13:40:07 +00:00)


In [ ]:
# preserving order
embeddings_tuples = [key_value_pair for key_value_pair in embeddings_dict.items()]
embeddings_dict = OrderedDict(embeddings_tuples)

time: 194 ms (started: 2021-02-26 13:40:33 +00:00)


In [ ]:
embeddings = np.array([embeddings_dict[i] for i in embeddings_dict])
embeddings.shape

(231239, 256)

time: 395 ms (started: 2021-02-26 13:40:35 +00:00)


In [ ]:
N = len(embeddings)
# split in groups of size
X = embeddings[:N]
X.shape

(231239, 256)

time: 3.95 ms (started: 2021-02-26 13:40:36 +00:00)


In [ ]:
# Hyperparameters
n_neighbors = list(map(int, (N*0.001,)))
n_components = [64]
min_dist = [0.3] # UMAP

total_length = np.prod(list(map(len, [n_neighbors, n_components, min_dist])))
print(f"Neighbors: {n_neighbors}")
print(f"Total Length: {total_length}")

Neighbors: [231]
Total Length: 1
time: 5.68 ms (started: 2021-02-26 13:41:19 +00:00)


In [ ]:
from itertools import product
from sklearn import manifold
import umap
from time import time

for n_neigh, n_comps, min_distance in tqdm(product(n_neighbors, n_components, min_dist), total=total_length):
    print(f"Neighbors: {n_neigh}, components: {n_comps}, min_distance: {min_distance}")
    reducer = umap.UMAP(
        n_components=n_comps,
        n_neighbors=n_neigh,
        min_dist=min_distance,
        n_jobs=-1,
        low_memory=True
    )
    t0 = time()
    Y = reducer.fit_transform(X)
    t1 = time()
    print(f"Time taken: {(t1-t0)/60:0.2f} minutes.")
    curr_tuples_embeddings = (
        (author_id, Y[i, :]) 
        for i, author_id in enumerate(embeddings_dict)
        if i < Y.shape[0]
    )
    curr_dict_embeddings = OrderedDict(curr_tuples_embeddings)
    filename = f"embedding_dim_{n_comps}_{n_neigh}_{min_distance}.npy"
    np.save(filename, curr_dict_embeddings)
    print(f"{filename} saved!\n")
    del reducer, Y, curr_tuples_embeddings, curr_dict_embeddings

Neighbors: 231, components: 64, min_distance: 0.3
Time taken: 30.92 minutes.
embedding_dim_64_231_0.3.npy saved!


time: 31min 19s (started: 2021-02-26 13:41:30 +00:00)
